# 1Hive Economy and Honey Supply Model

This notebook contains an abstract model of the 1hive economy, where outflows from the common pool are used to produce inflows and explores how this dynamic would impact a proposed change in the Honey supply policy which would mint and burn honey based on a target ratio between the common pool and total supply. 

In order to use the model we must make some assumptions about system dynamics, these assumptions include things we can control, like how the protocol behaves, and things we can't control like how humans and the market as a whole behaves. Since we cannot know for certain what to expect from things we cannot control, we can do our best to design and parameterize the protocol such that it behaves acceptably accross a broad range simulated situations. 

## The Model 

We assume that **outflows** from the common pool will be used **productively** to create applications which utilize Honey. These products may contain mechanism which capture a portion of cashflows as Honey and returns them as **inflows** back to the common pool. 

**Price** of Honey is modeled a stochasitc process that is correlated with a "fundamental" valuation heuristic. We model this as a correlated random walk towards a price target determined by the level of market saturation, market size, and circulating supply. 

A production function is used to translate outflows into marginal **production** and **market sauturation**. Production depends on the current price of Honey, outflows, and current level of prodution and results in the level of market saturation. 

A dynamic supply policy will **mint** or **burn** tokens from the common pool in order to target a ratio between common pool balance and total supply. Adjustments are made proportionally to distance from the desired ratio and are bounded by a throttle parameter which limits the magnitude of these changes over time. 

## Parameters

### Outflow Rate

We use conviction voting to allocate Honey from the common pool, conviction voting is parameterized such that there is a theoretical upper bound on the rate at which proposals can allocate funds, but the actual rate of spending depends on individuals staking on proposals. For the purpose of the model, we abstract the flow of funds from the common pool as a simple outflow rate parameter, which controls how much honey is moved from the common pool into circulating supply each time step. 

### Productivity

We know that in order to produce inflows, outflows must be used productively, this is an abstraction and simplification of a relatively complex process that we know exists. The actual value of the productivity parameter is hard to relate to real life, but we know that if its too low we wont reach market saturation, and if its too high we would reach market saturation impossibly quick. Practically speaking, a realisitic value for productivity is likely within a range where both success and failure are possible, because its in that range where marginal increases or decreases productivity and other parameters will have material difference on outcomes. Within that range we can explore different parameter choices, and pick parameter choices that tend to produce more successful outcomes for a broader range of assumed productivity values.

### Price Dynamics

Price dynamics have a significant impact on the behavior of the model, impacting both production as well the rate at which captured inflows move Honey from circulating supply back into the common pool. Currently price dynamics can be adjusted using the **variance** and **pull** parameters. Variance determines the magnitude of price movements, while pull determines the probability of moving towards the target price. 

A pull of `0.5` will approximate a truly random walk, decoupling price from production and market saturation. Whereas a pull of `1` would result in price changes always moving in the direction of the target. A high pull and low variance will tend to closely approximate the deterministic price target. 

### Throttle 

The throttle parameter determines the maximum adjustment made by the supply policy over time, If outflows exceed inflows it becomes the maximum rate of issuance, and if inflows exceed outflows, it becomes the maximum rate of burning from the common pool. 

We know stakeholders would prefer to have a predictable and low issuance rate, the throttle allows us to set an upper bound on the issuance rate, but we also know that if there is too little issuance we will be unlikely reach market saturation. 

If the throttle parameter is set to 0, the supply policy will be able to make unbounded adjustments. 

### Target Reserve Ratio

The target reserve ratio determines the ratio between the common pool and total supply, when the ratio is too high Honey in the common pool will be burned, and when it is too low Honey will be minted. 

## Planned Analysis

1. Use a historic average for outflow rate, a target reserve ratio of `0.2`, a throttle of `0.008` which works out to be 9.6% per year, variance of `0.25` and pull of `0.75`, determine a range of producitivity values where the trend of market saturation is bellow 0.1 and above 0.8.
2. Using the median value in that range for productivity, and do a parameter sweep of target reserve ratio from `0.1` and `0.3`in increments of `0.025`, and throttle beteen `0.002` and `0.032` in increments of `0.004`. Plot the market saturation trend and compare between simulations. 
3. Narrow the bounds of reserve and throttle and add parameter sweeps for productivity, variance, and pull. 
    


Use a heatmap for each variation of reserve and throttle, showing final market saturation and one for price using throttle and reserve as the x and y axis and color coding to represent value. 




In [1]:
import random as rand
import numpy as np 

In [2]:
# # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # 
# List of all the state variables in the system and their initial values
genesis_states = {
    'reserve': 7473, # Current common pool balance
    'circulation': 18765, # Total honey supply minus common pool balance (26238 - 7473)
    'size': 100000, # Total market size in terms of fiat inflows per month  
    'saturation': 0.0, # Percent of market captured by 1hive
    'production': 0.0, # Production state accounting for outflows and upkeep
    'utility': 0.0, # representing diminishing marginal returns on production
    'price': 10, # modeled as a random walk biased towards a target price based on size, saturation, circulation, and valuation ratio parameter. 
    'target_price':10, # Tracks the implied valuation based on our assumptions and influeces the stochastic spot price. 
    'netflow': 0.0,
    'adjustment': 0.0
}
# # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # 

# Model Params
We define some parameters which can be used to tune the behavior of issuance and distribution in the model. Paramters assume that each time step of the model relfect 1 month of real time, the simulation will run for 120 timesteps giving the model as a whole a 10 year time horizon.  

In [3]:
# # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # 
# List of all the state variables in the system and their initial values
params = {
    'throttle': [0.002, 0.004, 0.008, 0.002, 0.004, 0.008, 0.002, 0.004, 0.008], # maximimum proportion of the total supply that can be adjusted in each timestep 
    'outflow_rate': [0.05], # max proportion of common pool funds that can be spent each timestep 
    'target_reserve_ratio': [0.1, 0.1, 0.1, 0.2, 0.2, 0.2, 0.3, 0.3, 0.3], # target ratio of common pool funds to total supply
    'valuation_ratio': [2], # ratio of price to inflows (monthly) when at market saturation 
    # 'productivity': [0.87, 0.88, 0.89, .9],  # scalar parameter to determine impact of outflows on market saturation
    'productivity': [0.88],
    'growth': [0], # rate at which the market size will grow each time step 
    'p_variance': [.25], # variance of price changes
    'p_pull': [.75] # odds of moving towards or away from price target, a value of .5 is an unbiased random walk. 
}
# # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # 

# Timestep
We assume that each timestep in cadcad represents 1 month in real time, scaling model parameters to reflect that timescale. 

# Policies and State Update Functions

We define a supply policy and four state update fuctions. 


In [4]:
def supply_policy(params, step, sH, s):

    # first we calculate outlflow as a function of the reserve, outflow boundary, and saturation
    outflow = s['reserve'] * params['outflow_rate'] 
    
    # then we calculate inflow as a function size, saturation, price
    inflow = s['size'] * s['saturation'] / s['target_price']
    
    netflow = inflow - outflow

    # then we calculate current state
    reserve = s['reserve'] + netflow 
    circulation = s['circulation'] - netflow
    supply = reserve + circulation
    ratio = reserve / supply
    

    # Proportional control https://en.wikipedia.org/wiki/Proportional_control
    # corrections are made proportionally to the difference between the target and the current value

    # e = (params['target_reserve_ratio'] - ratio) / 12
    e = (1 - ratio / params['target_reserve_ratio'])/12

    if params['throttle'] != 0: 
        # Corrections bounded by a maximum issuance rate parameter 
        if e < 0:
            adjustment = max(e, -params['throttle']) * supply
        else:
            adjustment = min(e, params['throttle']) * supply 
    else:
        # Corrections are unbounded, issuance is bounded by the maximum outflow rate 
        adjustment = e * supply 


    return ({'netflow':netflow, 'adjustment':adjustment})


def saturation_process(params, step, sH, s):

    # outflows are a function of outflow_boundary parameter and current saturation
    # as saturation approaches 1, outflow_boundary is reduced by half. 
    outflow = s['reserve'] * params['outflow_rate'] 

    # production reduced by the maintainance parameter and then increased by the impact of outflows, which depends on the productivity paramater and the current price. 
    # production = s['production'] * (1 - params['maintainence']) + outflow * params['productivity'] * s['price']
    production = s['production'] * (params['productivity'] ** 2) + outflow * (1 + params['productivity']) * s['price']
    # production = s['production'] + outflow * params['productivity'] * s['price']

    # Utility represents the diminishing returns to production and is bounded at 10, we use the size value to shape the curve because it relates to the maximum inflows and steady state outflows. 
    utility = 10 * production / ( production + s['size'] )
    # utility = log

    # saturation modeled as a logistic function, shifted by 6 so that a 0 utility means near 0 saturation, a utility of 5 is around the inflection point, and 10 is near 1. 
    saturation = 1 / (1 + np.exp(-utility + 6))

    # size is a function of current size and growth rate
    size = s['size'] * (1 + params['growth'])


    return ({ 'saturation':saturation, 'size':size, 'utility':utility, 'production':production})

def price_policy(params, step, sH, s):
    # price follows a random walk that is pulled towards a target price. 

    # First we calculate the target price as a function of the size, valuation ratio, and state of the supply
    potential_inflows_per_token = s['size'] / (s['circulation'] + s['reserve'])
    # valuation ratio decreases as system reaches market saturation 
    adjusted_valuation_ratio = params['valuation_ratio'] / max(0.5, s['saturation'])
    # Price increases exponentially as the ratio of circulating supply to total supply decreases
    supply_sensitivity = 1 / (s['circulation'] / (s['circulation'] + s['reserve']) ) ** 2 

    target_price = potential_inflows_per_token * adjusted_valuation_ratio * supply_sensitivity

    # Price adjusts from previous timestep as a random walk, with a probability of moving closer to the price target determined by a parameter p_pull. 
    
    if np.random.random() < params['p_pull']: # toward target
        if s['price'] < target_price:
            direction = 1
        else:
            direction = -1 
    else: # away from target
        if s['price'] < target_price:
            direction = -1 
        else:
            direction = 1

    magnitude = np.abs(np.random.normal(0,params['p_variance']))

    price = s['price'] + s['price'] * direction * magnitude 

    return ({'price':price, 'target_price':target_price})

def update_reserve(params, step, sH, s, _input):
    key = 'reserve'
    value = s['reserve'] + _input['netflow'] + _input['adjustment']
    return (key, value)

def update_utility(params, step, sH, s, _input):
    key = 'utility'
    value = _input['utility']
    return (key, value)

def update_production(params, step, sH, s, _input):
    key = 'production'
    value = _input['production']
    return (key, value)

def update_circulation(params, step, sH, s, _input):
    key = 'circulation'
    value = s['circulation'] - _input['netflow']
    return (key, value)

def update_size(params, step, sH, s, _input):
    key = 'size'
    value =  _input['size']
    return (key, value)

def update_saturation(params, step, sH, s, _input):
    key = 'saturation'
    value =  _input['saturation']
    return (key, value)

def update_price(params, step, sH, s, _input):
    key = 'price'
    value = _input['price']
    return (key, value)

def update_target_price(params, step, sH, s, _input):
    key = 'target_price'
    value = _input['target_price']
    return (key, value)

def update_netflow(params, step, sH, s, _input):
    key = 'netflow'
    value =  _input['netflow']
    return (key, value)

def update_adjustment(params, step, sH, s, _input):
    key = 'adjustment'
    value =  _input['adjustment']
    return (key, value)

# Partial State Update Blocks


In [5]:
# # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # 
# In the Partial State Update Blocks, the user specifies if state update functions will be run in series or in parallel
partial_state_update_blocks = [
    { 
        'policies': {
            'supply_policy': supply_policy,
            'saturation_process': saturation_process,
            'price_policy': price_policy

        },
        'variables': { # The following state variables will be updated simultaneously
            'reserve': update_reserve,
            'circulation': update_circulation,
            'netflow': update_netflow,
            'adjustment': update_adjustment,
            'price': update_price,
            'target_price': update_target_price,
            'saturation': update_saturation,
            'utility': update_utility,
            'size': update_size,
            'production': update_production
        }
    }
]
# # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # 

# Simulation Configuration Parameters
Lastly, we define the number of timesteps and the number of Monte Carlo runs of the simulation. These parameters must be passed in a dictionary, in `dict_keys` `T` and `N`, respectively. In our example, we'll run the simulation for 10 timesteps. And because we are dealing with a deterministic system, it makes no sense to have multiple Monte Carlo runs, so we set `N=1`. We'll ignore the `M` key for now and set it to an empty `dict`

In [6]:
# # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # 
# Settings of general simulation parameters, unrelated to the system itself
# `T` is a range with the number of discrete units of time the simulation will run for;
# `N` is the number of times the simulation will be run (Monte Carlo runs)
# In this example, we'll run the simulation once (N=1) and its duration will be of 10 timesteps
# We'll cover the `M` key in a future article. For now, let's omit it
sim_config_dict = {
    'T': range(120),
    'N': 10,
    'M': params
}
# # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # 

# Putting it all together
We have defined the state variables of our system and their initial conditions, as well as the state update functions, which have been grouped in a single state update block. We have also specified the parameters of the simulation (number of timesteps and runs). We are now ready to put all those pieces together in a `Configuration` object.

In [7]:
#imported some addition utilities to help with configuration set-up
from cadCAD.configuration.utils import config_sim
from cadCAD.configuration import Experiment
from cadCAD import configs

exp = Experiment()
c = config_sim(sim_config_dict)
# # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # # 
# The configurations above are then packaged into a `Configuration` object
del configs[:]
exp.append_configs(initial_state=genesis_states, #dict containing variable names and initial values
                       partial_state_update_blocks=partial_state_update_blocks, #dict containing state update functions
                       sim_configs=c #preprocessed dictionaries containing simulation parameters
                      )

# Running the engine
We are now ready to run the engine with the configuration defined above. Instantiate an ExecutionMode, an ExecutionContext and an Executor objects, passing the Configuration object to the latter. Then run the `execute()` method of the Executor object, which returns the results of the experiment in the first element of a tuple.

In [8]:
%%capture
from cadCAD.engine import ExecutionMode, ExecutionContext
exec_mode = ExecutionMode()
local_mode_ctx = ExecutionContext(exec_mode.local_mode)

from cadCAD.engine import Executor

simulation = Executor(exec_context=local_mode_ctx, configs=configs) # Pass the configuration object inside an array
raw_system_events, tensor_field, sessions = simulation.execute() # The `execute()` method returns a tuple; its first elements contains the raw results


# Analyzing the results
We can now convert the raw results into a DataFrame for analysis

In [63]:
%matplotlib inline
import pandas as pd
simulation_result = pd.DataFrame(raw_system_events)
simulation_result['total_supply'] = simulation_result['reserve'] + simulation_result['circulation']
simulation_result['market_cap'] = simulation_result['total_supply'] * simulation_result['price']
simulation_result['ratio'] = simulation_result['reserve'] / simulation_result['total_supply']
simulation_result.set_index(['subset', 'run', 'timestep', 'substep'])

# See https://stackoverflow.com/a/34032549
import itertools

# parameter_1 = [0.002, 0.004, 0.008, 0.002, 0.004, 0.008, 0.002, 0.004, 0.008]
# parameter_2 = [0.1, 0.1, 0.1, 0.2, 0.2, 0.2, 0.3, 0.3, 0.3]
#parameter_1 = [0.002, 0.004, 0.008]
#parameter_2 = [0.1, 0.2, 0.3]
# parameter_sweep = list(itertools.product(parameter_1, parameter_2))

#cartesian_product = itertools.product(parameter_2, parameter_1)

#(parameter_1, parameter_2) = zip(*cartesian_product)

#p = list(zip(parameter_1, parameter_2)) 
#t =  [a * 121 for a in p] 
#flat_list = [item for sublist in t for item in sublist]

# simulation_result.index = flat_list 

# simulation_result
# print(t)

df = pd.DataFrame(simulation_result)
df = df.assign(**configs[0].sim_config['M'])
for i, (_, n_df) in enumerate(df.groupby(['simulation', 'subset', 'run'])):
    df.loc[n_df.index] = n_df.assign(**configs[i].sim_config['M'])
    
param_cols = configs[0].sim_config['M'].keys()
df = df.set_index(['simulation', 'run', *param_cols])


# Analysis 

After adding in concepts for market saturation, productivity and diminishing marginal returns of outflows, and a pricing function we can see how the system evolves with various paramater choices.  

With sufficient **productivity** relative to maintainence, the system stabilizes near the top of the logistic curve representing market saturation. We see market cap increase while saturating the market, then stabilize and remain steady. Price increases faster during the growth phases, but continues to steadily increases after reaching market saturation as the circulating supply decreases as a result of steady inflows. 


In [64]:



import plotly.express as px
fig = px.scatter(
    df.reset_index(),
    x='timestep',
    y=['total_supply', 'circulation', 'reserve'],
    facet_row='throttle',
    opacity=0.1,
    trendline='lowess',
    height=800,
    template='seaborn'
)

fig.update_layout(
    margin=dict(l=20, r=20, t=20, b=20),
)

fig.show()

In [11]:
fig = px.scatter(
    simulation_result,
    x='timestep',
    y=['netflow', 'adjustment'],
    facet_row='subset',
    opacity=0.1,
    trendline='lowess',
    height=800,
    template='seaborn'
)

fig.update_layout(
    margin=dict(l=20, r=20, t=20, b=20),
)

fig.show()

In [12]:
fig = px.scatter(
    simulation_result,
    x='timestep',
    y=['saturation'],
    facet_row='subset',
    opacity=0.1,
    trendline='lowess',
    height=800,
    template='seaborn'
)

fig.update_layout(
    margin=dict(l=20, r=20, t=20, b=20),
)

fig.show()

In [13]:
fig = px.scatter(
    simulation_result,
    x='timestep',
    y=['price'],
    facet_row='subset',
    opacity=0.1,
    trendline='lowess',
    height=800,
    template='seaborn'
)

fig.update_layout(
    margin=dict(l=20, r=20, t=20, b=20),
)

fig.show()

In [14]:
fig = px.scatter(
    simulation_result,
    x='timestep',
    y=['market_cap'],
    facet_row='subset',
    opacity=0.1,
    trendline='lowess',
    height=800,
    template='seaborn'
)

fig.update_layout(
    margin=dict(l=20, r=20, t=20, b=20),
)

fig.show()

In [15]:
fig = px.scatter(
    simulation_result,
    x='timestep',
    y=['utility'],
    facet_row='subset',
    opacity=0.1,
    trendline='lowess',
    height=800,
    template='seaborn'
)

fig.update_layout(
    margin=dict(l=20, r=20, t=20, b=20),
)

fig.show()